
<a id='chap-tpdeeplearning1'></a>

# Travaux pratiques - Introduction à l’apprentissage profond (*deep learning*)

L’objectif de cette première séance de travaux pratiques est de vous faire implémenter par vous même l’apprentissage de réseaux de neurones simples.

Cettre prise en main sera très formatrice pour utiliser des modèles plus évolués et comprendre le fonctionnement des libaries (comme Keras) où l’apprentissage est automatisé.

Nousa travaillerons avec la base de données image MNIST, constituée d’images de caractères manuscrits (60000 images en apprentissage, 10000 en test).

Voici le code permettant de récupérer les données  :

In [1]:
from keras.datasets import mnist
# the data, shuffled and split between train and test sets
(X_train, y_train), (X_test, y_test) = mnist.load_data()
# Reshape each 28x28 image -> 784 dim. vector
X_train = X_train.reshape(60000, 784)
X_test = X_test.reshape(10000, 784)
X_train = X_train.astype('float32')
X_test = X_test.astype('float32')
# Normalization
X_train /= 255
X_test /= 255
print(X_train.shape[0], 'train samples')
print(X_test.shape[0], 'test samples')

60000 train samples
10000 test samples


## Exercice 0 : visualisation de quelques images de la base


<dl style='margin: 20px 0;'>
<dt>Nous commencerons par afficher les 200 premières images de la base d’apprentissage.</dt>
<dd>
- Écrire un script `exo0.py` qui récupère les données avec le code précédent.  
- Compléter `exo0.py` pour permettre l’affichage demandé en utilisant le code suivant :  


> 

In [2]:
import matplotlib as mpl
mpl.use('TKAgg')
import matplotlib.pyplot as plt

plt.figure(figsize=(7.195, 3.841), dpi=100)
for i in range(200):
    plt.subplot(10,20,i+1)
    plt.imshow(X_train[i,:].reshape([28,28]), cmap='gray')
    plt.axis('off')
plt.show()


</dd>

</dl>

Le script `exo0.py` doit produire l’affichage ci-dessous :

<img src="_images/exo0.png" style="height:400px;" align="center">

## Question :

Quel est l’espace dans lequel se trouvent les images ? Quelle est sa taille ?

## Exercice 1 : Régression Logistique

### Modèle de prédiction

Nous commencerons par créer un modèle de classification linéaire populaire, la régression logistique. Ce modèle correspond à un réseau de neurones à une seule couche, qui va projeter le vecteur d’entrée $ \mathbf{x_i} $ pour une image MNIST (taille $ 28^2=784 $) avec un vecteur de de paramètres $ \mathbf{w_{c}} $ pour chaque classe (plus un biais $ b_c $). Pour correspondre à la matrice des données de l’exercice précédent, on considère que chaque exemple $ \mathbf{x_i} $ est un vecteur ligne - taille (1,784).

En regroupant l’ensemble des jeux de paramètres $ \mathbf{w_{c}} $ pour les 10 classes dans une matrice $ \mathbf{W} $ (taille $ 784\times 10 $) et les biais dans un vecteur $ \mathbf{b} $, on obtient un vecteur $ \mathbf{\hat{s_i}} =\mathbf{x_i}  \mathbf{W}  + \mathbf{b} $ de taille (1,10).

Une fonction d’activation de type soft-max sur $ \mathbf{\hat{y_i}} = $ `softmax` $ (\mathbf{s_i}) $ permet d’obtenir le vecteur de sortie prédit par le modèle $ \mathbf{\hat{y_i}} $ - de taille (1,10) - qui représente la probabilité *a posteriori* $ p(\mathbf{\hat{y_i}} | \mathbf{x_i}) $ pour chacune des 10 classes :


<a id='equation-softmax'></a>
$$
p(\hat{y_{c,i}} | \mathbf{x_i}) ) = \frac{e^{\langle \mathbf{x_i} ; \mathbf{w_{c}}\rangle + b_{c}}}{\sum\limits_{c'=1}^{10} e^{\langle \mathbf{x_i} ; \mathbf{w_{c'}}\rangle + b_{c'}}} \tag{1}
$$

Le schéma ci-dessous illustre le modèle de régression logistique avec un réseau de neurones.

<img src="_images/LR.png" style="height:150px;" align="center">

Quel est le nombre de paramètres du modèle ? Justifier le calcul.

### Formulation du problème d’apprentissage

Afin d’entraîner le réseau de neurones, on va comparer, pour chaque exemple d’apprentissage, la sortie prédite $ \mathbf{\hat{y_i}} $ par le réseau (équation [(1)](#equation-softmax)) pour l’image $ \mathbf{x_i} $ avec la sortie réelle $ \mathbf{y_i^*} $ issue de la supervision qui correspond à la catégorie de l’image $ \mathbf{x_i} $: on utilisera en encodage de type *one-hot* pour $ \mathbf{y_i^*} $, *i.e.* :


<a id='equation-one-hot'></a>
$$
y_{c,i}^* =
 \begin{cases}
   1 & \text{si c correspond à l'indice de la classe de } \mathbf{x_i}  \\
   0 & \text{sinon}
 \end{cases} \tag{2}
$$

Pour mesurer l’erreur de prédiction, on utilisera une fonction de coût de type entropie croisée (*cross-entropy*) entre $ \mathbf{\hat{y_i}} $ et $ \mathbf{y_i^*} $ (l’entropie croisée est liée à la divergence de Kullback-Leiber, qui mesure une dissimilarité entre distributions de probabilités) :
$ \mathcal{L}(\mathbf{\hat{y_i}}, \mathbf{y_i^*}) = -\sum\limits_{c=1}^{10} y_{c,i}^* log(\hat{y}_{c,i}) = - log(\hat{y}_{c^*,i}) $, où $ c^* $ correspond à l’indice de la classe donnée par la supervision pour l’image $ \mathbf{x_i} $.

La fonction de coût finale consistera à moyenner l’entropie croisée sur l’ensemble de la base d’apprentissage $ \mathcal{D} $ constituée de $ N=60000 $ images :


<a id='equation-ce'></a>
$$
\mathcal{L}_{\mathbf{W},\mathbf{b}}(\mathcal{D})  = - \frac{1}{N}\sum_{i=1}^{N} log(\hat{y}_{c^*,i}) \tag{3}
$$

### Question :

La fonction de coût de [(3)](#equation-ce) est-elle convexe par rapport aux paramètres $ \mathbf{W} $, $ \mathbf{b} $ du modèle ? Avec un pas de gradient bien choisi, peut-on assurer la convergence vers le minimum  global de la solution ?

### Optimisation du modèle

Afin d’optimiser les paramètres $ \mathbf{W} $ et $ \mathbf{b} $ du modèle de régression logistique par descente de gradient, on va utiliser la règle des dérivées chaînées (*chain rule*) :

$$
\frac{\partial \mathcal{L}}{\partial \mathbf{W}} =  \frac{1}{N}\sum_{i=1}^{N} \frac{\partial \mathcal{L}}{\partial \mathbf{\hat{y_i}}}  \frac{\partial \mathbf{\hat{y_i}}}{\partial \mathbf{s_i}} \frac{\partial \mathbf{s_i}}{\partial \mathbf{W}}
$$

$$
\frac{\partial \mathcal{L}}{\partial \mathbf{b}} =  \frac{1}{N}\sum_{i=1}^{N} \frac{\partial \mathcal{L}}{\partial \mathbf{\hat{y_i}}}  \frac{\partial \mathbf{\hat{y_i}}}{\partial \mathbf{s_i}} \frac{\partial \mathbf{s_i}}{\partial \mathbf{b}}
$$

### Montrer que :

$$
\frac{\partial \mathcal{L}}{\partial \mathbf{s_i}} = \mathbf{\delta^y_i} = \frac{\partial \mathcal{L}}{\partial \mathbf{\hat{y_i}}}  \frac{\partial \mathbf{\hat{y_i}}}{\partial \mathbf{s_i}} = \mathbf{\hat{y_i}} - \mathbf{y_i^*}
$$

### En déduire que les gradients de $ \mathcal{L} $ par rapport aux paramètres du modèle s’écrivent :


<a id='equation-gradientw'></a>
$$
\frac{\partial \mathcal{L}}{\partial \mathbf{W}} = \frac{1}{N} \mathbf{X}^T (\mathbf{\hat{Y}} - \mathbf{Y^*}) = \frac{1}{N} \mathbf{X}^T \mathbf{\Delta^y} \tag{4}
$$


<a id='equation-gradientb'></a>
$$
\frac{\partial \mathcal{L}}{\partial \mathbf{b}} = \frac{1}{N}\sum_{i=1}^{N}(\mathbf{\hat{y_i}} - \mathbf{y_i^*}) \tag{5}
$$

où  $ \mathbf{X} $ est la matrice des données (taille $ 60000\times 784 $), $ \mathbf{\hat{Y}} $ est la matrice des labels prédits sur l’ensemble de la base d’apprentissage (taille $ 60000\times 10 $) et $ \mathbf{Y^*} $ est la matrice des labels issue de la supervision (*ground truth*, taille $ 60000\times 10 $), et $ \mathbf{\Delta^y}=\mathbf{\hat{Y}}-\mathbf{Y^*} $.

### Implémentation de l’apprentissage

Les gradients aux équations [(8)](tpDeepLearning2.ipynb#equation-gradientw) et [(9)](tpDeepLearning2.ipynb#equation-gradientb) s’écrivent sous forme « vectorielle », ce qui rend les calculs efficaces avec des librairies de calculs scientifique comme `numpy`. Après calcul du gradient, les paramètres seront mis à jour de la manière suivante :


<a id='equation-gradientupdatew'></a>
$$
\mathbf{W}^{(t+1)} = \mathbf{W}^{(t)} - \eta \frac{\partial \mathcal{L}}{\partial \mathbf{W}} \tag{6}
$$


<a id='equation-gradientupdateb'></a>
$$
\mathbf{b}^{(t+1)} = \mathbf{b}^{(t)} - \eta \frac{\partial \mathcal{L}}{\partial \mathbf{b}} \tag{7}
$$

où $ \eta $ est le pas de gradient (*learning rate*).

Pour implémenter l’algorithme d’apprentissage, on utilisera une descente de gradient stochastique, c’est à dire que les gradients aux équations [(8)](tpDeepLearning2.ipynb#equation-gradientw) et [(9)](tpDeepLearning2.ipynb#equation-gradientb) ne seront pas calculés sur l’ensemble des $ N=60000 $ images d’apprentissage, mais sur un sous-ensemble appelé **batch** (contenant $ tb $ exemples). Cette technique permet une mise à jour des paramètres plus fréquente qu’avec une descente de gradient classique, et une convergence plus rapide (au détriment d’un calcul de gradient approximé).

**On demande de mettre en place un script** `exo1.py` **qui implémente l’algorithme de régression logistique sur la base MNIST.**

Après avoir chargé les données (exercice 0), on utilisera le code suivant pour générer des étiquettes (*labels*) au format 0-1 encoding - [(2)](#equation-one-hot).

In [3]:
from keras.utils import np_utils
K=10
# convert class vectors to binary class matrices
Y_train = np_utils.to_categorical(y_train, K)
Y_test = np_utils.to_categorical(y_test, K)

On mettra alors en place un code dont le squellette est donné ci-dessous :

In [4]:
import numpy as np
N = X_train.shape[0]
d = X_train.shape[1]
W = np.zeros((d,K))
b = np.zeros((1,K))
numEp = 20 # Number of epochs for gradient descent
eta = 1e-1 # Learning rate
batch_size = 100
nb_batches = int(float(N) / batch_size)
gradW = np.zeros((d,K))
gradb = np.zeros((1,K))

for epoch in range(numEp):
    for ex in range(nb_batches):
     # FORWARD PASS : compute prediction with current params for examples in batch
     # BACKWARD PASS :
     # 1) compute gradients for W and b
     # 2) update W and b parameters with gradient descent
    
    
    #####~~~~~~ VOIR CORRECTION DERNIERE CELLULE ~~~~~~######

SyntaxError: unexpected EOF while parsing (<ipython-input-4-5ff72cfc9342>, line 21)

Pour compléter ce code, vous devez :

- Mettre en place une fonction `forward(batch, W, b)` qui va calculer la prédiction pour un batch de données. La fonction `forward` sera appelée pour chaque itération de la double boucle précédente.  
- Si on considère un batch des données de taille $ tb\times 784 $, les paramètres $ \mathbf{W} $ (taille $ 784\times 10 $) et $ \mathbf{b} $ (taille $ 1\times 10 $), la fonction `forward` renvoie la prédiction $ \mathbf{\hat{Y}} $ sur le batch (taille $ tb\times 10 $).  
- On pourra utiliser la fonction suivante pour calculer la fonction softmax sur chaque élément de de la matrice de la projection linéraire (taille $ tb\times 10 $) :  

In [5]:
def softmax(X):
 # Input matrix X of size Nbxd - Output matrix of same size
 E = np.exp(X)
 return (E.T / np.sum(E,axis=1)).T

- Compléter le code pour la passe *backward*, consistant à :  
- Calculer les gradients comme indiqué dans les équations [(8)](tpDeepLearning2.ipynb#equation-gradientw) et [(9)](tpDeepLearning2.ipynb#equation-gradientb).  
- Mettre à jour les paramètres par descente de gradient comme indiqué dans les équations [(6)](#equation-gradientupdatew) et [(7)](#equation-gradientupdateb).  


Enfin, vous pouvez utiliser la fonction `accuracy(W, b, images, labels)` fournie pour calculer le taux de bon classement (bonne reconnaissance) du modèle. Ceci permet de mesurer l’évolution des performances au cours des époques de l’algorithme d’apprentissage, et sur la base de test une fois le modèle appris.

**Vous devez obtenir un score de l’ordre de 92% sur la base de test pour ce modèle de régression logistique.**

In [6]:
def accuracy(W, b, images, labels):
  pred = forward(images, W,b )
  return np.where( pred.argmax(axis=1) != labels.argmax(axis=1) , 0.,1.).mean()*100.0

In [7]:
def softmax(X): 
    # Input matrix X of size Nbxd
    E = np.exp(X)
    return (E.T / np.sum(E,axis=1)).T

def forward(images, W, b):             
    pred = np.matmul(images, W) + b
    return softmax(pred)

In [9]:
import numpy as np
N = X_train.shape[0]
d = X_train.shape[1]
W = np.zeros((d,K))
b = np.zeros((1,K))
numEp = 20 # Number of epochs for gradient descent
eta = 1e-1 # Learning rate
batch_size = 100
nb_batches = int(float(N) / batch_size)
gradW = np.zeros((d,K))
gradb = np.zeros((1,K))

for epoch in range(numEp):
    for ex in range(nb_batches):
     # FORWARD PASS : compute prediction with current params for examples in batch
     # BACKWARD PASS :
     # 1) compute gradients for W and b
     # 2) update W and b parameters with gradient descent
        
        X = X_train[ex*batch_size:(ex+1)*batch_size,:]
        Y = Y_train[ex*batch_size:(ex+1)*batch_size,:]  
        Ypred = forward(X, W, b)      
        Yval = Ypred - Y
        # BACKWARD 
        gradW = 1.0/batch_size * np.matmul(np.transpose(X_train[ex*batch_size:(ex+1)*batch_size,:]),Yval)
        gradb = 1.0/batch_size * (Yval.sum(axis=0)).reshape((1,10))  

        W = W - eta * gradW
        b = b - eta * gradb
    print("epoch ", epoch, "accurcy train=",accuracy(W, b, X_train, Y_train), "accurcy test=",accuracy(W, b, X_test, Y_test))  

epoch  0 accurcy train= 89.27333333333334 accurcy test= 90.24
epoch  1 accurcy train= 90.33 accurcy test= 90.91
epoch  2 accurcy train= 90.92833333333333 accurcy test= 91.36999999999999
epoch  3 accurcy train= 91.25333333333333 accurcy test= 91.60000000000001
epoch  4 accurcy train= 91.45333333333333 accurcy test= 91.7
epoch  5 accurcy train= 91.62333333333333 accurcy test= 91.81
epoch  6 accurcy train= 91.74833333333333 accurcy test= 91.86999999999999
epoch  7 accurcy train= 91.85 accurcy test= 91.95
epoch  8 accurcy train= 91.96 accurcy test= 92.04
epoch  9 accurcy train= 92.035 accurcy test= 92.04
epoch  10 accurcy train= 92.09 accurcy test= 92.13
epoch  11 accurcy train= 92.17333333333333 accurcy test= 92.14
epoch  12 accurcy train= 92.23333333333333 accurcy test= 92.15
epoch  13 accurcy train= 92.25999999999999 accurcy test= 92.15
epoch  14 accurcy train= 92.31166666666667 accurcy test= 92.21000000000001
epoch  15 accurcy train= 92.36666666666666 accurcy test= 92.22
epoch  16 accu